In [1]:
import time

In [2]:
import numpy as np
import pandas as pd

In [3]:
import dask.dataframe as dd
import dask.array as da
import dask.bag as db

# import dask_xgboost

In [4]:
import gcsfs
import pickle

# Read Data with Dask

In [5]:
import dask.distributed
cluster = dask.distributed.LocalCluster()
client = dask.distributed.Client(cluster)

In [6]:
ddf = dd.read_parquet("gs://emtek-cdp-prod-ml/ato/vidio-pollingsmoker-heuristic-dataset/*.parquet", engine="pyarrow")

In [7]:
ddf = ddf.set_index('visitor_id')

In [8]:
featureColumns = [x for x in ddf.columns if not(x in ['visitor_id','is_smoker'])]

In [9]:
ddf = ddf.loc[ddf['is_smoker'].notnull(), :]

In [10]:
ddf = ddf.fillna(0)

In [11]:
X = ddf.loc[:,featureColumns]#.compute()
y = ddf['is_smoker']#.compute()

In [12]:
from dask_ml.model_selection import train_test_split

In [13]:
X_train, X_test, Y_train, Y_test = train_test_split(
    X, y, 
    test_size=0.15, random_state=69) 

/opt/conda/miniconda3/lib/python3.8/site-packages/dask_ml/model_selection/_split.py:462: FutureWarning: The default value for 'shuffle' must be specified when splitting DataFrames. In the future DataFrames will automatically be shuffled within blocks prior to splitting. Specify 'shuffle=True' to adopt the future behavior now, or 'shuffle=False' to retain the previous behavior.
  warnings.warn(


In [14]:
X_train, X_eval, Y_train, Y_eval = train_test_split(
    X_train, Y_train, 
    test_size=0.10, random_state=69) 

# ML - XGBoost
https://xgboost.readthedocs.io/en/stable/tutorials/dask.html

## ML Train

In [14]:
import xgboost as xgb

In [15]:
params = {'objective': 'binary:logistic',
          'max_depth': 4, 'eta': 0.0001, 'subsample': 0.8,
          'min_child_weight': 0.5,
          'eval_metric': ['logloss', 'auc', 'aucpr']
         }

In [16]:
# bst = dask_xgboost.train(client, 
#    params, 
#    X_train, Y_train, 
#    num_boost_round=100, 
#    early_stopping_rounds=20,
#    evals_result=[(X_train, Y_train), (X_eval, Y_eval)]
# )

In [18]:
dtrain = xgb.dask.DaskDMatrix(client, X_train, Y_train)

distributed.worker - ERROR - Worker stream died during communication: tcp://127.0.0.1:36367
Traceback (most recent call last):
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/comm/core.py", line 286, in connect
    comm = await asyncio.wait_for(
  File "/opt/conda/miniconda3/lib/python3.8/asyncio/tasks.py", line 501, in wait_for
    raise exceptions.TimeoutError()
asyncio.exceptions.TimeoutError

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py", line 2057, in gather_dep
    response = await get_data_from_worker(
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py", line 3327, in get_data_from_worker
    return await retry_operation(_get_data, operation="get_data_from_worker")
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/utils_comm.py", line 384, in retry_operation
    return aw

In [19]:
deval = xgb.dask.DaskDMatrix(client, X_eval, Y_eval)

distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

In [20]:
model = xgb.dask.train(client, 
       params, dtrain, 
       num_boost_round=100, 
       early_stopping_rounds=20,
       evals=[(dtrain, "train"), (deval, "eval")]
)

/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/client.py:3480: RuntimeWarning: coroutine 'Client._update_scheduler_info' was never awaited
  self.sync(self._update_scheduler_info)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
[03:53:52] WARNING: ../src/gbm/gbtree.cc:129: Tree method is automatically selected to be 'approx' for distributed training.[03:53:52] WARNING: ../src/gbm/gbtree.cc:129: Tree method is automatically selected to be 'approx' for distributed training.
[03:53:52] WARNING: ../src/gbm/gbtree.cc:129: Tree method is automatically selected to be 'approx' for distributed training.

[03:53:52] WARNING: ../src/gbm/gbtree.cc:129: Tree method is automatically selected to be 'approx' for distributed training.
[03:53:52] WARNING: ../src/gbm/gbtree.cc:129: Tree method is automatically selected to be 'approx

task [xgboost.dask]:tcp://127.0.0.1:46415 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:46415 got new rank 3
task [xgboost.dask]:tcp://127.0.0.1:43015 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:43015 got new rank 11
task [xgboost.dask]:tcp://127.0.0.1:33197 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:33197 got new rank 2
task [xgboost.dask]:tcp://127.0.0.1:33547 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:33547 got new rank 1
task [xgboost.dask]:tcp://127.0.0.1:42909 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:42909 got new rank 0
task [xgboost.dask]:tcp://127.0.0.1:37559 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:37559 got new rank 9
task [xgboost.dask]:tcp://127.0.0.1:44083 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:44083 got new rank 10
task [xgboost.dask]:tcp://127.0.0.1:44017 connected to the tracker
task [xgboost.dask]:tcp://127.0.0.1:44017 got new rank 8
task [

In [21]:
bst = model['booster']

In [23]:
fs = gcsfs.GCSFileSystem(project='emtek-cdp-prod')
filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-xgb_v000.pkl'

with fs.open(filename, 'wb') as file:
    pickle.dump(bst, file)

## ML Predict

In [24]:
fs = gcsfs.GCSFileSystem(project='emtek-cdp-prod')
filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-xgb_v000.pkl'

with fs.open(filename, 'rb') as file:
    bst = pickle.load(file)

In [25]:
pdf = pd.read_parquet("gs://emtek-cdp-prod-ml/ato/vidio-pollingsmoker-heuristic-dataset/part-00199-8e24ec82-c8c7-453e-bce4-61a82e340271-c000.snappy.parquet")
X_test_pdf = pdf.loc[:, featureColumns]
dtest_pdf = xgb.DMatrix(X_test_pdf)

In [26]:
Y_test_pdf_pred_1 = bst.predict(dtest_pdf)

In [27]:
Y_test_pdf_pred_1

array([0.5013395 , 0.49984545, 0.5013395 , ..., 0.5010469 , 0.4997012 ,
       0.5013395 ], dtype=float32)

# ML - Tensorflow
https://ml.dask.org/keras.html

## ML Train

In [15]:
import tensorflow as tf
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.models import Sequential

2022-06-29 14:48:18.403150: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: :/usr/lib/hadoop/lib/native
2022-06-29 14:48:18.403192: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [16]:
from tensorflow.keras.optimizers import Adam

In [17]:
num_feature = X_train.shape[1]
num_classes  = 1 # Y_train.shape[1]

In [18]:
# def build_model(num_feature, num_class, lr=0.001):
#     model = Sequential()

#     model.add(Dense(2000, activation='relu', input_dim=num_feature))
#     model.add(Dense(4000, activation='relu'))
#     model.add(Dense(num_class, activation='sigmoid'))

#     model.compile(loss='binary_crossentropy', optimizer=Adam(learning_rate = lr), metrics=['AUC', 'Precision'])

#     return model

In [19]:
def build_model(num_feature, num_class, lr=0.001):
    model = Sequential()

    model.add(Dense(2000, activation='relu', input_dim=num_feature))
    model.add(Dropout(0.4))
    model.add(Dense(4000, activation='relu'))
    model.add(Dropout(0.4))
    model.add(Dense(num_class, activation='sigmoid'))

    model.compile(loss='binary_crossentropy', optimizer=Adam(learning_rate = lr), metrics=['AUC', 'Precision'])

    return model

In [20]:
from scikeras.wrappers import KerasClassifier

In [21]:
niceties = dict(verbose=False)

In [22]:
model_1 = KerasClassifier(
    build_fn=build_model, 
    num_feature=num_feature, 
    num_class=num_classes, 
    lr=0.0001, 
    **niceties
)

In [46]:
# history = model_1.fit(X_train, Y_train, 
#     verbose=1, epochs=100, batch_size=64, 
#     validation_split=0.2,
#     validation_data=(X_test, Y_test)
# )

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

Epoch 1/100
590/590 [==============================] - ETA: 0s - loss: 0.7580 - auc: 0.5440 - precision: 0.3595

ValueError: Failed to find data adapter that can handle input: <class 'dask.dataframe.core.DataFrame'>, <class 'dask.dataframe.core.Series'>

In [47]:
# history = model_1.fit(X_train, Y_train, 
#     verbose=1, epochs=100, batch_size=64, 
#     validation_split=0.2
#  )

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
tornado.application - ERROR - Exception in callback functools.partial(<bound method IOLoop._discard_future_result of <tornado.platform.asyncio.AsyncIOLoop object at 0x7fbe8db769a0>>, <Task finished name='Task-42938' coro=<Worker.heartbeat() done, defined at /opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py:930> exception=RuntimeError('dictionary changed size during iteration')>)
Traceback (most recent call last):
  File "/opt/conda/miniconda3/lib/python3

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 20% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

Epoch 1/100
472/472 [==============================] - 11s 22ms/step - loss: 0.7915 - auc: 0.5329 - precision: 0.3522 - val_loss: 0.8123 - val_auc: 0.5632 - val_precision: 0.0000e+00
Epoch 2/100
472/472 [==============================] - 10s 21ms/step - loss: 0.6962 - auc: 0.5710 - precision: 0.3814 - val_loss: 0.6379 - val_auc: 0.5961 - val_precision: 0.5192
Epoch 3/100
472/472 [==============================] - 10s 20ms/step - loss: 0.6819 - auc: 0.5861 - precision: 0.4209 - val_loss: 0.6247 - val_auc: 0.6028 - val_precision: 0.4244
Epoch 4/100
472/472 [==============================] - 10s 20ms/step - loss: 0.6513 - auc: 0.6097 - precision: 0.4311 - val_loss: 0.6239 - val_auc: 0.6082 - val_precision: 0.4524
Epoch 5/100
472/472 [==============================] - 10s 20ms/step - loss: 0.6434 - auc: 0.6232 - precision: 0.4806 - val_loss: 0.6831 - val_auc: 0.5860 - val_precision: 0.3520
Epoch 6/100
472/472 [==============================] - 9s 20ms/step - loss: 0.6322 - auc: 0.6359 - pr

Epoch 47/100
472/472 [==============================] - 9s 20ms/step - loss: 0.3259 - auc: 0.9140 - precision: 0.8443 - val_loss: 1.4818 - val_auc: 0.5584 - val_precision: 0.3956
Epoch 48/100
472/472 [==============================] - 9s 20ms/step - loss: 0.3207 - auc: 0.9171 - precision: 0.8455 - val_loss: 1.6137 - val_auc: 0.5650 - val_precision: 0.3893
Epoch 49/100
472/472 [==============================] - 9s 20ms/step - loss: 0.3172 - auc: 0.9194 - precision: 0.8529 - val_loss: 1.6123 - val_auc: 0.5559 - val_precision: 0.3925
Epoch 50/100
472/472 [==============================] - 9s 20ms/step - loss: 0.3138 - auc: 0.9203 - precision: 0.8551 - val_loss: 1.6635 - val_auc: 0.5655 - val_precision: 0.3973
Epoch 51/100
472/472 [==============================] - 9s 20ms/step - loss: 0.3085 - auc: 0.9246 - precision: 0.8619 - val_loss: 1.7332 - val_auc: 0.5552 - val_precision: 0.3874
Epoch 52/100
472/472 [==============================] - 9s 20ms/step - loss: 0.3036 - auc: 0.9258 - preci

Epoch 93/100
472/472 [==============================] - 9s 20ms/step - loss: 0.2278 - auc: 0.9593 - precision: 0.9105 - val_loss: 2.8832 - val_auc: 0.5592 - val_precision: 0.3958
Epoch 94/100
472/472 [==============================] - 9s 20ms/step - loss: 0.2276 - auc: 0.9592 - precision: 0.9090 - val_loss: 2.8697 - val_auc: 0.5539 - val_precision: 0.4102
Epoch 95/100
472/472 [==============================] - 9s 20ms/step - loss: 0.2304 - auc: 0.9579 - precision: 0.9066 - val_loss: 2.8887 - val_auc: 0.5501 - val_precision: 0.4001
Epoch 96/100
472/472 [==============================] - 9s 20ms/step - loss: 0.2250 - auc: 0.9601 - precision: 0.9093 - val_loss: 3.0364 - val_auc: 0.5408 - val_precision: 0.3877
Epoch 97/100
472/472 [==============================] - 9s 20ms/step - loss: 0.2301 - auc: 0.9584 - precision: 0.9000 - val_loss: 2.9194 - val_auc: 0.5559 - val_precision: 0.4013
Epoch 98/100
472/472 [==============================] - 9s 20ms/step - loss: 0.2200 - auc: 0.9614 - preci

In [150]:
history = model_1.fit(X_train, Y_train, 
    verbose=1, epochs=100, batch_size=64, 
    validation_split=0.2
 )

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 20% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 20% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

Epoch 1/100
472/472 [==============================] - 12s 24ms/step - loss: 0.8381 - auc: 0.5200 - precision: 0.3445 - val_loss: 0.6478 - val_auc: 0.5791 - val_precision: 0.4043
Epoch 2/100
472/472 [==============================] - 11s 22ms/step - loss: 0.7602 - auc: 0.5489 - precision: 0.3624 - val_loss: 0.6551 - val_auc: 0.5804 - val_precision: 0.0000e+00
Epoch 3/100
472/472 [==============================] - 11s 22ms/step - loss: 0.6878 - auc: 0.5687 - precision: 0.3866 - val_loss: 0.6586 - val_auc: 0.5700 - val_precision: 0.4048
Epoch 4/100
472/472 [==============================] - 11s 22ms/step - loss: 0.6752 - auc: 0.5746 - precision: 0.3686 - val_loss: 0.6533 - val_auc: 0.5848 - val_precision: 1.0000
Epoch 5/100
472/472 [==============================] - 11s 22ms/step - loss: 0.6549 - auc: 0.5898 - precision: 0.3742 - val_loss: 0.6265 - val_auc: 0.6070 - val_precision: 0.5172
Epoch 6/100
472/472 [==============================] - 11s 22ms/step - loss: 0.6521 - auc: 0.6000 - p

472/472 [==============================] - 11s 23ms/step - loss: 0.3840 - auc: 0.8796 - precision: 0.8161 - val_loss: 1.4037 - val_auc: 0.5744 - val_precision: 0.4193
Epoch 92/100
472/472 [==============================] - 11s 23ms/step - loss: 0.3802 - auc: 0.8826 - precision: 0.8119 - val_loss: 1.4257 - val_auc: 0.5740 - val_precision: 0.4199
Epoch 93/100
472/472 [==============================] - 11s 23ms/step - loss: 0.3788 - auc: 0.8821 - precision: 0.8160 - val_loss: 1.4477 - val_auc: 0.5716 - val_precision: 0.4160
Epoch 94/100
472/472 [==============================] - 11s 23ms/step - loss: 0.3792 - auc: 0.8823 - precision: 0.8157 - val_loss: 1.4097 - val_auc: 0.5787 - val_precision: 0.4145
Epoch 95/100
472/472 [==============================] - 11s 23ms/step - loss: 0.3768 - auc: 0.8841 - precision: 0.8195 - val_loss: 1.4315 - val_auc: 0.5716 - val_precision: 0.4106
Epoch 96/100
472/472 [==============================] - 11s 23ms/step - loss: 0.3774 - auc: 0.8837 - precision: 0

In [151]:
fs = gcsfs.GCSFileSystem(project='emtek-cdp-prod')
# filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-tf_v000.pkl'
filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-tf_v001_dropout.pkl'

with fs.open(filename, 'wb') as file:
    pickle.dump(model_1, file)

## ML Predict

In [49]:
fs = gcsfs.GCSFileSystem(project='emtek-cdp-prod')
filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-tf_v000.pkl'

with fs.open(filename, 'rb') as file:
    model = pickle.load(file)

In [52]:
pdf = pd.read_parquet("gs://emtek-cdp-prod-ml/ato/vidio-pollingsmoker-heuristic-dataset/part-00199-8e24ec82-c8c7-453e-bce4-61a82e340271-c000.snappy.parquet")
X_test_pdf = pdf.loc[:, featureColumns].fillna(0)

In [55]:
Y_test_pdf_pred_2 = model.predict_proba(X_test_pdf)

In [56]:
Y_test_pdf_pred_2

array([[7.0979548e-01, 2.9020455e-01],
       [5.5984908e-01, 4.4015092e-01],
       [5.6144947e-01, 4.3855053e-01],
       ...,
       [1.0000000e+00, 2.7396070e-26],
       [7.4541569e-04, 9.9925458e-01],
       [7.2981822e-01, 2.7018175e-01]], dtype=float32)

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)


# ML - Tensorflow with CrossVal

## ML Train

In [23]:
from dask_ml.model_selection import KFold

In [24]:
# index_X_train = X_train.to_dask_array(lengths=True)
# index_Y_train = Y_train.to_dask_array(lengths=True)

In [25]:
from scikeras.wrappers import KerasClassifier

niceties = dict(verbose=False)

model_1 = KerasClassifier(
    build_fn=build_model, 
    num_feature=num_feature, 
    num_class=num_classes, 
    lr=0.0001, 
    **niceties
)

In [26]:
t0 = time.perf_counter()

In [27]:
kfold = KFold(n_splits=3)
kf = kfold.split(X_train.to_dask_array(lengths=True), Y_train.to_dask_array(lengths=True))

tornado.application - ERROR - Exception in callback functools.partial(<bound method IOLoop._discard_future_result of <tornado.platform.asyncio.AsyncIOLoop object at 0x7f0bd54f4910>>, <Task finished name='Task-1131' coro=<Worker.heartbeat() done, defined at /opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py:930> exception=RuntimeError('dictionary changed size during iteration')>)
Traceback (most recent call last):
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/tornado/ioloop.py", line 741, in _run_callback
    ret = callback()
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/tornado/ioloop.py", line 765, in _discard_future_result
    future.result()
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py", line 941, in heartbeat
    executing={
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py", line 941, in <dictcomp>
    executing={
RuntimeError: dictionary changed size during iteration
dist

In [28]:
t1 = time.perf_counter()
print(t1-t0)
t0 = time.perf_counter()

474.57022277599935


In [29]:
for k, (idx_train, idx_test) in enumerate(kf):
    print("------ Iter: {} ------".format(k))
    print(idx_train, idx_test)
    npart = X_train.npartitions
    index_train  = X_train.index.to_dask_array(lengths=True)[idx_train]
    index_train = index_train.rechunk(chunks=int(np.ceil(len(index_train) / npart)))
    X_train_rp = X_train\
        .loc[index_train]\
        .repartition(npartitions=npart)
    Y_train_rp = Y_train\
        .loc[index_train]\
        .repartition(npartitions=npart)
    model_1.fit(
        X_train_rp, 
        Y_train_rp
    )

------ Iter: 0 ------
dask.array<concatenate, shape=(25152,), dtype=int64, chunksize=(1406,), chunktype=numpy.ndarray> dask.array<concatenate, shape=(12577,), dtype=int64, chunksize=(645,), chunktype=numpy.ndarray>


distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

...

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

       'c01fefdf-6ce4-405e-80d2-b79d92a4d3e5',
       'c0229c93-cab6-4cd4-817e-0d88bcc5b277',
       'c023a5e9-ecfc-4ce9-a573-2a58fc7220ea',
       'c023b547-f4dc-4eee-a818-d3961b4600ef',
       'c02d203e-fe1c-41cc-9142-36a61cf4d3b7',
       'c02dcac2-1bb4-4000-9a8d-67d1d0093f66',
       'c031a938-edb4-48d9-ae17-71f81aa040f4',
       'c032fb3d-de74-4612-9f5e-0b350b407cbf',
       'c034d43b-2d25-4b94-82d0-febd5d056edd',
       'c0361f31-ec14-4e29-9eaf-b0f9b2a2d7ee',
       'c03822be-2a92-4011-8dae-3248fa1de558',
       'c03bc3c6-82a1-480a-8815-a60625e69f7a',
       'c03e0b53-9d04-43a4-85d2-979c9eec8d3a',
       'c03f3b27-4a6a-42d8-95fa-998ba73a8d31',
       'c041bba7-2f5b-4da6-8205-64eca39170a1',
       'c041c63e-e558-4ff2-9420-3e0b1cb52444',
       'c0450364-411f-4ece-a075-82d8c4ce23a7',
       'c046bd1b-b347-4773-875a-76bd4ccd8b5c',
       'c047c80a-a300-4b5f-817c-653f41d473a1',
       'c0483d98-90c6-43aa-8212-793ffd6b0dd7',
       'c048
kwargs:    {}
Exception: ValueError('Length of 

distributed.worker - WARNING -  Compute Failed
Function:  Series
args:      (array(['63c51875-b6ae-40fa-8d98-7c699d970e48',
       '63c67424-5b4a-49f8-bf7f-d6eb510a0212',
       '63c85558-bd76-4800-8bf4-83e6550c52af',
       '63c8cd27-031a-44f8-a444-5fbc12759699',
       '63c8d8f8-0635-4d4b-ae2a-b6958f6e8b83',
       '63ca3ea9-e04e-435b-b9ce-bb3e8736322f',
       '63ca4d0c-fab5-47d7-ae36-b3c615532e00',
       '63cabc89-fd53-4fbd-a006-66128917d057',
       '63cb68b4-94ce-4ef6-835e-f80138b1c859',
       '63cbf2db-1206-416d-875e-773d0e3dad30',
       '63cf94c9-0078-4338-8625-e667077d8715',
       '63d082cf-5b69-423f-852a-568b50d41193',
       '63d2083d-9115-4ab2-ade3-641d6a34bd1d',
       '63d34264-0eb2-4a2a-a730-1341c081b325',
       '63d54405-05dd-48a9-8f54-dc9a96e7001c',
       '63d79c10-8c41-4491-aeed-e3c748d4fb66',
       '63db4d40-1485-48e3-96e9-3d1d4749b1a3',
       '63dd2ab5-ca75-4fe2-a8e1-8495912d9d3f',
       '63dd7d54-708b-4a8a-b2c0-7553341f5e82',
       '63de7f5d-2448-4d1e-a0b

ValueError: Length of passed values is 126, index implies 43.

In [65]:
X_train_rp = X_train.loc[index_train]
Y_train_rp = Y_train.loc[index_train]

In [66]:
X_train_rp.head(10)

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

ValueError: Length of passed values is 126, index implies 0.

In [ ]:
X_train.index.map_partitions(lambda x: len(x)).compute()

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

In [ ]:
X_train.map_partitions()

In [57]:
tmp.shape

(nan, 1332)

In [51]:
index_train

dask.array<rechunk-merge, shape=(25152,), dtype=object, chunksize=(126,), chunktype=numpy.ndarray>

In [37]:
X_train_rp.npartitions

200

In [38]:
Y_train_rp.npartitions

200

In [47]:
X_train_rp.partitions[199]

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [48]:
Y_train_rp.partitions[199]

Dask Series Structure:
npartitions=1
ffff43aa-045c-49ba-804f-e5139bcb37b4    bool
ffffff0d-3e88-4776-91c7-5e25701b37b1     ...
Name: is_smoker, dtype: bool
Dask Name: blocks, 40079 tasks

In [36]:
model_1.fit(
        X_train_rp, 
        Y_train_rp
)

distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

ValueError: Length of passed values is 126, index implies 28.

distributed.core - ERROR - Exception while handling op heartbeat_worker
Traceback (most recent call last):
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/core.py", line 493, in handle_comm
    result = handler(comm, **msg)
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/scheduler.py", line 2196, in heartbeat_worker
    ws._executing = {
  File "/opt/conda/miniconda3/lib/python3.8/site-packages/distributed/scheduler.py", line 2197, in <dictcomp>
    self.tasks[key]: duration for key, duration in executing.items()
KeyError: "('slice_with_int_dask_array_aggregate-1f1dbccda230bbb375de43c4ce78d14f', 124)"
tornado.application - ERROR - Exception in callback functools.partial(<bound method IOLoop._discard_future_result of <tornado.platform.asyncio.AsyncIOLoop object at 0x7fb545347910>>, <Task finished name='Task-37711' coro=<Worker.heartbeat() done, defined at /opt/conda/miniconda3/lib/python3.8/site-packages/distributed/worker.py:930> exception=Ke

In [34]:
for k, (idx_x, idx_y) in enumerate(kf):
    print("------ Iter: {} ------".format(k))
    print(idx_x, idx_y)
    index_x = X_train.index.to_dask_array(lengths=True)[idx_x]
    index_y  = Y_train.index.to_dask_array(lengths=True)[idx_y]
    model_1.fit(
        X_train.repartition(npartitions=index_x.numblocks[0]).loc[index_x], 
        Y_train.repartition(npartitions=index_y.numblocks[0]).loc[index_y]
    )

------ Iter: 0 ------
dask.array<concatenate, shape=(25152,), dtype=int64, chunksize=(1406,), chunktype=numpy.ndarray> dask.array<concatenate, shape=(12577,), dtype=int64, chunksize=(645,), chunktype=numpy.ndarray>


distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

...

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

5f199875-d00b-4623-9616-b7b0db210f91              16  ...                         0.0
5f1b93f8-f207-41bc-8bec-3a832a2c9
kwargs:    {}
Exception: ValueError('Length of passed values is 336, index implies 592.')

distributed.worker - WARNING -  Compute Failed
Function:  execute_task
args:      ((subgraph_callable,                                       total_play_all  ...  vod_num_content_genre_yoga
visitor_id                                            ...                            
57c3a155-966f-4b7d-af47-704c5a6e4b7c             148  ...                         0.0
57c3abbe-16ac-433b-ae1a-6ac9f6cef8d0              13  ...                         0.0
57c41a20-2da6-4680-b144-670929331c75              37  ...                         0.0
57c59efb-d1e1-4aab-b415-0919c04e3f66               2  ...                         0.0
57c5cda2-4528-4696-a4f5-ed53acc548a5               8  ...                         0.0
...                                              ...  ...                         ..

distributed.worker - WARNING -  Compute Failed
Function:  execute_task
args:      ((subgraph_callable,                                       total_play_all  ...  vod_num_content_genre_yoga
visitor_id                                            ...                            
ac255aa3-9221-4073-baf6-1ce22a2b2696              10  ...                         0.0
ac2723e8-40a1-45b4-b2ab-2f5d01377621              40  ...                         0.0
ac2e9131-7e8a-494f-aa93-929d62b28e63              21  ...                         0.0
ac2f8bde-0ab8-4750-bb36-bfa573d29632              11  ...                         0.0
ac30bfd2-9fcf-49ea-ad33-b03c70a3600c              69  ...                         0.0
...                                              ...  ...                         ...
aee49fef-7c3b-43ea-b126-7dd48c07192b               1  ...                         0.0
aee61237-5659-4463-9c51-1e70d5be3922              34  ...                         0.0
aee97e69-b5dc-4ff0-a6be-2f120f33238f 

ValueError: Length of passed values is 28, index implies 183.

In [ ]:
for k, (idx_x, idx_y) in enumerate(kf):
    print("------ Iter: {} ------".format(k))
    print(idx_x, idx_y)
    index_x = X_train.index.to_dask_array(lengths=True)[idx_x]
    index_y  = Y_train.index.to_dask_array(lengths=True)[idx_y]
    X_train_rp = X_train.repartition(npartitions=index_x.numblocks[0]).loc[index_x.rechunk(chunks=int(np.ceil(len(index_x) / index_x.numblocks[0])))]
    Y_train_rp = Y_train.repartition(npartitions=index_y.numblocks[0]).loc[index_y.rechunk(chunks=int(np.ceil(len(index_y) / index_y.numblocks[0])))]
    model_1.fit(
        X_train_rp, 
        Y_train_rp
    )

In [ ]:
t1 = time.perf_counter()
print(t1-t0)

In [ ]:
fs = gcsfs.GCSFileSystem(project='emtek-cdp-prod')
# filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-tf_v000.pkl'
# filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-tf_v001_dropout.pkl'
filename = 'gs://emtek-cdp-prod-configs/jupyter-notebooks/ATO/test-ds-pipeline/model-tf_v001_dropout_cv.pkl'

with fs.open(filename, 'wb') as file:
    pickle.dump(model_1, file)

distributed.worker - WARNING -  Compute Failed
Function:  Series
args:      (array(['c4f00071-aea4-4c27-8b2a-f3802d2d9ebf',
       'c4f6f129-6a04-410b-ab84-310ff4358778',
       'c4f9af21-d500-4151-9b81-69cd95f55291',
       'c4fa2817-28f0-4824-be0c-c91a32dbf25a',
       'c4fa2dfa-42e4-4106-a3c9-b41114782ce7',
       'c4fba242-3bdf-4a5d-b9af-ba57bbfb905f',
       'c4fbc8cc-80f1-44a4-a2bc-5bf5ed5bb898',
       'c50038b8-7618-4a1b-a4a6-939614402421',
       'c502a460-860a-4a04-8111-56442e1e13b6',
       'c503a337-9a86-4bae-875b-4c2053a30276',
       'c50af47b-ba3f-43b1-994a-419b164947e4',
       'c50c753a-f2c5-43b3-87fd-a6cc1c5b27ec',
       'c512b791-08a6-4126-a617-d9a49b615e2c',
       'c5155267-af50-43a9-b17b-849b9876b8b7',
       'c5183991-339c-4893-9298-77c6cae2e7d2',
       'c51ac86e-b84f-46e7-91bd-6ae87cfafc73',
       'c51c4445-e024-47dc-8d6f-5071200c728a',
       'c5239a88-9ca4-444c-a848-833e0343be8e',
       'c5276746-36db-4464-a2d0-72a0b4a55ce0',
       'c5307afa-a2ba-44e1-a1d

       '8f30cc45-dab4-4b03-b874-c60a5cbe5100',
       '8f316765-4c21-4639-b00c-a456dd754f18',
       '8f32a594-7c5e-40e4-b094-1af5d895dfda',
       '8f32b823-64ef-4771-a3ff-4c7a4f5099d5',
       '8f32e391-fd32-4bc8-a311-c369b39e93b2',
       '8f34da83-8b96-48d6-bc48-b85e89716c37',
       '8f357bad-ed3f-4c9b-bed0-8bde0c57f603',
       '8f3704bf-7760-41a9-8253-496dd2a367bb',
       '8f376e49-2c57-4f72-8c64-05c861eaf06e',
       '8f38
kwargs:    {}
Exception: ValueError('Length of passed values is 126, index implies 312.')

distributed.worker - WARNING -  Compute Failed
Function:  Series
args:      (array(['ed32e2a1-debc-4a38-b581-5e8fa629c66e',
       'ed33103e-03ef-40c5-82e4-d02ef69f80d4',
       'ed33c677-9470-40d4-8fe2-ea39c9c04e9e',
       'ed3663ea-a753-4829-a7b2-dd0ac857eeac',
       'ed374d37-cf4c-40e6-a5c1-a9758f613d8d',
       'ed378266-74bb-432b-b99b-9fbe77e12ba8',
       'ed381e68-b333-4821-851a-40910f2f67aa',
       'ed3c4ffb-c3be-40ca-a0bf-0b36b7870947',
       'ed3ddaa3-dc0

## ML Predict

## Coret2 (skippable)

In [52]:
index_x = index_train
index_y = index_test

In [47]:
X_train.npartitions

200

In [48]:
Y_train.npartitions

200

In [53]:
index_x.numblocks

(131,)

In [54]:
index_y.numblocks

(68,)

In [51]:
help(X_train.repartition)

Help on method repartition in module dask.dataframe.core:

repartition(divisions=None, npartitions=None, partition_size=None, freq=None, force=False) method of dask.dataframe.core.DataFrame instance
    Repartition dataframe along new divisions
    
    Parameters
    ----------
    divisions : list, optional
        List of partitions to be used. Only used if npartitions and
        partition_size isn't specified.
        For convenience if given an integer this will defer to npartitions
        and if given a string it will defer to partition_size (see below)
    npartitions : int, optional
        Number of partitions of output. Only used if partition_size
        isn't specified.
    partition_size: int or string, optional
        Max number of bytes of memory for each partition. Use numbers or
        strings like 5MB. If specified npartitions and divisions will be
        ignored.
    
        .. warning::
    
           This keyword argument triggers computation to determine
  

In [55]:
X_train.repartition(npartitions=index_x.numblocks[0]).loc[index_train]

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [63]:
help(da.rechunk)

Help on function rechunk in module dask.array.rechunk:

rechunk(x, chunks='auto', threshold=None, block_size_limit=None, balance=False)
    Convert blocks in dask array x for new chunks.
    
    Parameters
    ----------
    x: dask array
        Array to be rechunked.
    chunks:  int, tuple, dict or str, optional
        The new block dimensions to create. -1 indicates the full size of the
        corresponding dimension. Default is "auto" which automatically
        determines chunk sizes.
    threshold: int, optional
        The graph growth factor under which we don't bother introducing an
        intermediate step.
    block_size_limit: int, optional
        The maximum block size (in bytes) we want to produce
        Defaults to the configuration value ``array.chunk-size``
    balance : bool, default False
        If True, try to make each chunk to be the same size.
    
        This means ``balance=True`` will remove any small leftover chunks, so
        using ``x.rechunk(chun

In [64]:
help(X_train.to_dask_array)

Help on method to_dask_array in module dask.dataframe.core:

to_dask_array(lengths=None, meta=None) method of dask.dataframe.core.DataFrame instance
    Convert a dask DataFrame to a dask array.
    
    Parameters
    ----------
    lengths : bool or Sequence of ints, optional
        How to determine the chunks sizes for the output array.
        By default, the output array will have unknown chunk lengths
        along the first axis, which can cause some later operations
        to fail.
    
        * True : immediately compute the length of each partition
        * Sequence : a sequence of integers to use for the chunk sizes
          on the first axis. These values are *not* validated for
          correctness, beyond ensuring that the number of items
          matches the number of partitions.
    meta : object, optional
        An optional `meta` parameter can be passed for dask to override the
        default metadata on the underlying dask array.
    
    Returns
    -------

In [34]:
X_train

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [32]:
Y_train

Dask Series Structure:
npartitions=200
                                        bool
000077d9-2bf8-4963-b139-944349b16cc2     ...
                                        ... 
ffff43aa-045c-49ba-804f-e5139bcb37b4     ...
ffffff0d-3e88-4776-91c7-5e25701b37b1     ...
Name: is_smoker, dtype: bool
Dask Name: split, 10675 tasks

In [64]:
index_x

dask.array<slice_with_int_dask_array_aggregate, shape=(25152,), dtype=object, chunksize=(1406,), chunktype=numpy.ndarray>

In [30]:
index_y

dask.array<slice_with_int_dask_array_aggregate, shape=(12577,), dtype=object, chunksize=(645,), chunktype=numpy.ndarray>

In [74]:
int(np.ceil(len(index_x) / 200))

126

In [76]:
len(index_x) / 126

199.61904761904762

In [69]:
index_x.rechunk(chunks=X_train.npartitions)

dask.array<rechunk-merge, shape=(25152,), dtype=object, chunksize=(200,), chunktype=numpy.ndarray>

In [35]:
index_x.rechunk(chunks=int(np.ceil(len(index_x) / X_train.npartitions)))

dask.array<rechunk-merge, shape=(25152,), dtype=object, chunksize=(126,), chunktype=numpy.ndarray>

In [29]:
X_train.loc[index_x.rechunk(chunks=int(np.ceil(len(index_x) / X_train.npartitions)))]

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [28]:
Y_train.loc[index_y.rechunk(chunks=int(np.ceil(len(index_y) / Y_train.npartitions)))]

Dask Series Structure:
npartitions=200
                                        bool
000077d9-2bf8-4963-b139-944349b16cc2     ...
                                        ... 
ffff43aa-045c-49ba-804f-e5139bcb37b4     ...
ffffff0d-3e88-4776-91c7-5e25701b37b1     ...
Name: is_smoker, dtype: bool
Dask Name: loc-series, 25989 tasks

In [38]:
X_train.loc[index_x.rechunk(chunks=int(np.ceil(len(index_x) / X_train.npartitions)))].npartitions

200

In [39]:
Y_train.loc[index_y.rechunk(chunks=int(np.ceil(len(index_y) / Y_train.npartitions)))].npartitions

200

In [35]:
X_train.repartition(npartitions=index_x.numblocks[0]).loc[index_x]

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [42]:
Y_train.repartition(npartitions=index_y.numblocks[0]).loc[index_y]

Dask Series Structure:
npartitions=68
                                        bool
01542c8b-27d2-496f-8caa-23955e22ab0a     ...
                                        ... 
fa85b345-7d16-4edb-9fdb-0927dbf5c981     ...
ffffff0d-3e88-4776-91c7-5e25701b37b1     ...
Name: is_smoker, dtype: bool
Dask Name: loc-series, 25419 tasks

In [43]:
X_train.repartition(npartitions=index_x.numblocks[0]).loc[index_x].npartitions

131

In [44]:
Y_train.repartition(npartitions=index_y.numblocks[0]).loc[index_y].npartitions

68

In [37]:
X_train.repartition(npartitions=index_x.numblocks[0]).loc[index_x.rechunk(chunks=int(np.ceil(len(index_x) / index_x.numblocks[0])))]

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [30]:
X_train_rp

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [33]:
X_train.npartitions

200

In [31]:
X_train_rp.npartitions

200

In [34]:
Y_train_rp.npartitions

200

In [32]:
index_x.numblocks

(200,)

In [35]:
X_train

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [31]:
X_train_rp

Dask DataFrame Structure:
                                     total_play_all total_play_vod total_play_ls ls_num_content_channel_2022_pmpl_id_spring ls_num_content_channel_abc_australia ls_num_content_channel_afc_asian_cup_2023_qualifiers ls_num_content_channel_ajwa_tv ls_num_content_channel_aljazeera ls_num_content_channel_antv ls_num_content_channel_aov_star_league___asl__ ls_num_content_channel_arirang ls_num_content_channel_asia_road_racing_championship_2022 ls_num_content_channel_astra_international_may_2022 ls_num_content_channel_bein_1 ls_num_content_channel_bein_3 ls_num_content_channel_bellator ls_num_content_channel_beritasatu ls_num_content_channel_breaking_news_liputan6_sctv ls_num_content_channel_bundesliga ls_num_content_channel_cage_warriors ls_num_content_channel_celeb360 ls_num_content_channel_celeb_360 ls_num_content_channel_champions_tv_1 ls_num_content_channel_champions_tv_2 ls_num_content_channel_champions_tv_3 ls_num_content_channel_champions_tv_4 ls_num_content_channel_champions_tv_goal ls_num_content_channel_champions_tv_xtra ls_num_content_channel_citra_bioskop ls_num_content_channel_citra_culinary___travel ls_num_content_channel_citra_dangdut ls_num_content_channel_citra_drama ls_num_content_channel_citra_entertainment ls_num_content_channel_citra_muslim ls_num_content_channel_codashop_global_series ls_num_content_channel_configure_dash_playlist_duration_to_30_seconds ls_num_content_channel_da_vinci ls_num_content_channel_daai_tv ls_num_content_channel_daebak_byoode ls_num_content_channel_drawing_aff_cup ls_num_content_channel_drm ls_num_content_channel_duka_pemakaman_artis_lawas_ivo_nilakreshna ls_num_content_channel_dw_english ls_num_content_channel_eredivisie ls_num_content_channel_ets_drm_fhd_debug ls_num_content_channel_euro_news ls_num_content_channel_fashion_tv___global ls_num_content_channel_fashion_tv_midnight_secrets ls_num_content_channel_fashiontv_l_original ls_num_content_channel_fim_juniorgp ls_num_content_channel_friendly_match ls_num_content_channel_gr_astra_sustainability_webinar ls_num_content_channel_gr_perayaan_hut_ke_65_astra ls_num_content_channel_grand_launching_of_the_national_digital_talent_program_ ls_num_content_channel_grii_pusat ls_num_content_channel_hip_hip_horee_ ls_num_content_channel_holywings_sport_show ls_num_content_channel_horee ls_num_content_channel_iel_season_iv____grand_final ls_num_content_channel_iel_season_iv_best_moment ls_num_content_channel_iel_season_iv_best_playoff_highlight ls_num_content_channel_iel_season_iv_funny_moment ls_num_content_channel_iel_season_iv_highlights_group_stage ls_num_content_channel_iel_season_iv_triple_kill_highlights ls_num_content_channel_iel_season_iv_ultra_kill_moment ls_num_content_channel_iel_webinar_masterclass_series ls_num_content_channel_indosiar ls_num_content_channel_inspirato_sharing_session ls_num_content_channel_jaktv ls_num_content_channel_jumat_berkah ls_num_content_channel_jumat_keramat ls_num_content_channel_kamisfun_with_floridina ls_num_content_channel_ketawa_ala__62 ls_num_content_channel_kompas_tv ls_num_content_channel_krui_pro_2022___day_1 ls_num_content_channel_krui_pro_2022___day_2 ls_num_content_channel_krui_pro_2022___test_2 ls_num_content_channel_krui_pro_2022_test ls_num_content_channel_liputan6_update ls_num_content_channel_liputan_haji_2022 ls_num_content_channel_live_commentary_liverpool_vs_real_madrid ls_num_content_channel_live_streaming ls_num_content_channel_liverpool_tv ls_num_content_channel_makuku_air_diapers_comfort_launching_event ls_num_content_channel_meet_and_greet ls_num_content_channel_mentari_tv ls_num_content_channel_metro_tv ls_num_content_channel_misa_jumat_pertama_emtek ls_num_content_channel_misa_katedral ls_num_content_channel_misa_minggu ls_num_content_channel_msc_2022 ls_num_content_channel_mytv ls_num_content_channel_nba ls_num_content_channel_nba_tv ls_num_content_channel_net_tv ls_num_content_channel_news_asia ls_num_content_channel_nhk_world_japan ls_num_content_chann

In [30]:
Y_train_rp

Dask Series Structure:
npartitions=200
                                        bool
000077d9-2bf8-4963-b139-944349b16cc2     ...
                                        ... 
ffff43aa-045c-49ba-804f-e5139bcb37b4     ...
ffffff0d-3e88-4776-91c7-5e25701b37b1     ...
Name: is_smoker, dtype: bool
Dask Name: loc-series, 40078 tasks

In [34]:
len(X_train_rp)

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

ValueError: Length of passed values is 126, index implies 143.

In [ ]:
len(Y_train_rp)

In [40]:
index_x[:100].compute()

distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

array(['551f302e-6795-49d2-80f0-6403c5a5a5df',
       '551fd91b-e014-4f53-8b55-1edb8a57db4e',
       '5522e86d-ba24-4915-aaf0-c88d81f06d64',
       '552647f3-52ff-4c68-9451-5b64ccde43f2',
       '5527dbe9-3348-437f-a452-d5dabfc7b4af',
       '552C111E-F365-4360-9BC6-5BC78814F5A8',
       '552b3408-7711-4f3c-81b9-451796a1e733',
       '552d15e6-c33d-4e69-be69-93e23742e63d',
       '552da768-015d-4496-b4ed-f750bfee93a6',
       '553096f3-e860-4865-a063-4e9c5e6476cd',
       '5530B943-3782-4D07-A30F-275422216060',
       '5536959e-74c8-45be-82d8-b4ad5a8488e8',
       '5536c0ee-2dd5-4879-947a-6ae20e037c60',
       '5536d74e-a449-4766-90fa-9540bc2a5737',
       '553f2806-b87b-4e99-8df4-a70c79812df8',
       '554121d4-c461-47af-a14a-a48888e892ca',
       '554506c0-5f0c-45c7-a371-292c31fc1924',
       '55475e63-1103-4129-97ca-d17bc1b74d6e',
       '55486b15-d721-43ac-8b6c-65bdf4d8d319',
       '55489e7e-6d32-4423-a34a-186d2fc4ff27',
       '554cb18d-c6f2-4f61-abf1-91d3a09eb0fd',
       '554e6

In [ ]:
index_y[:100].compute()

distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 14% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 15% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

# (DIRTY) ML - Tensorflow with Validation_Data

## ML Train

In [129]:
class KerasClassifierMod(KerasClassifier):
#     def __init__(self):
#         super().__init__()

    def _unpack_x_y_val(self, data):
          if not isinstance(data, tuple):
            return (data, None, None)
          elif len(data) == 1:
            return (data[0], None, None)
          elif len(data) == 2:
            return (data[0], data[1], None)
          elif len(data) == 3:
            return (data[0], data[1], data[2])
        
    def _init_x_y_val(self, data):
        if data:
            X_val, y_val, _ = self._unpack_x_y_val(data)
            
#             # Data checks
#             if not ((super().warm_start) and super().initialized_):
#                 X_val, y_val = super()._initialize(X_val, y_val)
#             else:
#                 X_val, y_val = super()._validate_data(X_val, y_val)
#             super()._ensure_compiled_model()

            X_val, y_val = super()._validate_data(X_val, y_val)
            super()._ensure_compiled_model()
            
            y_val = super().target_encoder_.transform(y_val)
            X_val = super().feature_encoder_.transform(X_val)

            super()._check_model_compatibility(y_val)
        else:
            val_x = None
            val_y = None
        
        return (val_x, val_y)

    def fit(self, X, y, sample_weight=None, validation_data=None, **kwargs):
        # self.fit__validation_data = validation_data
        validation_data_trans = self._init_x_y_val(validation_data)

        super().fit(X, y, sample_weight=sample_weight, validation_data=validation_data_trans, **kwargs)
        # vars(self).pop('fit__validation_data')
        return self

In [130]:
# model_2 = KerasClassifier(
#     build_fn=build_model, 
#     num_feature=num_feature, 
#     num_class=num_classes, 
#     lr=0.0001, 
#     **niceties
# )

In [131]:
model_2 = KerasClassifierMod(
    build_fn=build_model, 
    num_feature=num_feature, 
    num_class=num_classes, 
    lr=0.0001, 
    **niceties
)

In [132]:
# history = model_1.fit(X_train, Y_train, 
#     verbose=1, epochs=100, batch_size=64, 
#     validation_split=0.2,
#     validation_data=(X_test, Y_test)
# )

In [133]:
history = model_2.fit(X_train, Y_train, 
    validation_data=(X_test, Y_test),
    verbose=1, epochs=100, batch_size=64, 
    validation_split=0.2
)

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 17% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 16% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 13% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
distributed.utils_perf - WARNING - full garbage collections took

AttributeError: 'KerasClassifierMod' object has no attribute 'y_dtype_'

distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
